In [1]:
import pandas as pd

pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

In [2]:

df = pd.read_csv(r'C:\Users\igors\Downloads\_data.csv')


In [3]:
df = df.set_index('ID  объявления')

In [4]:
# Удаляем ненужные столбцы
df = df.drop(columns=['Unnamed: 0', 'Телефоны', 'Серия дома', 'Тип'])
# Удаляем ненужные строки
df.drop(df[df['Адрес'].str.split(',').str[0] != 'Москва'].index, inplace=True)

In [5]:
df['city'] = df['Адрес'].apply(lambda x: x.split(',')[0])

In [6]:
# На сайте видно, что на первом месте всегда общая площадь
df['total_area'] = df['Площадь, м2'].apply(lambda x: float(x.split('/')[0]))

In [7]:
# Для удобства дальнейшего подсчета комнат заменим NaN значения на строковые значения
df['Количество комнат'].fillna('Unknown', inplace=True)

In [8]:
df['rooms_num'] = df['Количество комнат'].apply(lambda x: int(x.split(',')[0]) if x != 'Unknown' else x)

In [9]:
df['area_based_room_num'] = df['Площадь комнат, м2'].apply(lambda x: len(x.split()) if isinstance(x, str) else x)

In [10]:
mask = (df['rooms_num'] == 'Unknown') & (~df['area_based_room_num'].isna())
df.loc[mask, 'rooms_num'] = df.loc[mask, 'area_based_room_num']

In [11]:
# Находим строки, где значение столбца 'rooms_num' неизвестно, а в 'Описании' упоминается "студия" или "однокомнатность",
# и присваиваем им значение 1 в столбце 'rooms_num'
df.loc[(df['rooms_num'] == 'Unknown') & (df['Описание'].str.contains('студи|однок', case=False)), 'rooms_num'] = 1

In [12]:
df[~df['rooms_num'].isna()][['rooms_num', 'total_area']].groupby('rooms_num').agg({'total_area': 'median'})

total_area
rooms_num            
1                37.0
2                52.0
3                80.0
4               145.0
5               206.0
6               330.0
Unknown          25.0

In [13]:
# Заполним оставшиеся пропущенные значения ориентируясь на медианную площадь
df.loc[(df['rooms_num'] == 'Unknown') & (df['total_area'] < 52), 'rooms_num'] = 1
df.loc[(df['rooms_num'] == 'Unknown') & ~(df['total_area'] < 52), 'rooms_num'] = 2
df['rooms_num'].value_counts()

rooms_num
2    7411
1    7186
3    3668
4    1011
5     333
6     128
Name: count, dtype: int64

In [14]:
df['layout'] = df['Количество комнат'].apply(lambda x: x.split(',')[1].strip() if isinstance(x, str) and len(x.split(',')) > 1 else 'Unknown')

In [15]:
# Теперь заполним пропущенные значения в Количество комнат

df.loc[df['Количество комнат'] == 'Unknown', 'Количество комнат'] = df.loc[df['Количество комнат'] == 'Unknown', 'rooms_num']

In [16]:
df['layout'] = df['Количество комнат'].apply(lambda x: x.split(',')[1].strip() if isinstance(x, str) and len(x.split(',')) > 1 else 'Unknown')

In [17]:
df['layout'].value_counts()

layout
Unknown          11770
Изолированная     5803
Оба варианта      1492
Смежная            672
Name: count, dtype: int64

In [19]:
df['Метро'].fillna('Unknown', inplace=True)

In [20]:
df['metro'] = df['Метро'].apply(lambda x: x.split('(')[0])
df['metro'].count()

19737

In [21]:
df[df['metro'] == 'Unknown'][['Адрес', 'Название ЖК']].shape

(346, 2)

In [22]:
df.loc[(df['metro'] == 'Unknown') & (df['Адрес'].str.contains('зеленогр', case=False)), 'metro'] = 'Ховрино (25 мин на машине)'


In [23]:
df[df['metro'] == 'Unknown'][['Адрес', 'Название ЖК']].shape

(194, 2)

In [24]:
df.iloc[:,:6].info()

<class 'pandas.core.frame.DataFrame'>
Index: 19737 entries, 271271157 to 274672243
Data columns (total 6 columns):
 #   Column             Non-Null Count  Dtype 
---  ------             --------------  ----- 
 0   Количество комнат  19737 non-null  object
 1   Метро              19737 non-null  object
 2   Адрес              19737 non-null  object
 3   Площадь, м2        19737 non-null  object
 4   Дом                19737 non-null  object
 5   Парковка           8563 non-null   object
dtypes: object(6)
memory usage: 1.1+ MB


In [25]:
df['price'] = df['Цена'].apply(lambda x: int(x.split('.')[0]))

In [26]:
df['Парковка'].fillna('Unknown', inplace=True)

In [27]:
df.groupby('Парковка').agg({'price': 'median'})

price
Парковка                
Unknown          45000.0
многоуровневая   71000.0
на крыше         54000.0
наземная         45000.0
открытая         55000.0
подземная       110000.0

In [28]:
df['price'].info()

<class 'pandas.core.series.Series'>
Index: 19737 entries, 271271157 to 274672243
Series name: price
Non-Null Count  Dtype
--------------  -----
19737 non-null  int64
dtypes: int64(1)
memory usage: 308.4 KB


In [29]:
df['has_parkin'] = df['Парковка'].apply(lambda x: 0 if x == 'Unknown' else 1)

In [30]:
df.groupby('has_parkin').agg({'price': 'mean'})

price
has_parkin              
0           78273.701539
1           97381.812449

In [31]:
df[df['Название ЖК'].isin(df[(df['Парковка'] == 'Unknown') & (~df['Название ЖК'].isna())]['Название ЖК'])][['Парковка','Название ЖК']]

Парковка                                   Название ЖК
ID  объявления                                                              
271271157            подземная                             Новый Арбат, 2010
273614615              Unknown                                      The Book
274837728              Unknown                             Smolensky De Luxe
274839211            подземная                            Филипповский, 2002
274767901              Unknown                            Филипповский, 2002
274995950              Unknown                                      The Book
274945807              Unknown                                  Филипповский
273941734              Unknown                                The Book, 2020
223918678              Unknown                                  Филипповский
264664760              Unknown                                 Звёзды Арбата
228923308            подземная                                  Филипповский
273353104            подземная                                 Звёзды Арбата
273353103            подземная                                 Звёзды Арбата
268321690            подземная                           Звёзды Арбата, 2013
272188531              Unknown                                The Book, 2019
267110043              Unknown                       Smolensky De Luxe, 2015
265323319            подземная                                 Звёзды Арбата
271209314              Unknown                             Новый Арбат, 2010
241704098              Unknown                             Новый Арбат, 2010
239000331              Unknown                            Филипповский, 2002
274315381              Unknown                            Филипповский, 2002
269132104            подземная                                 Звёзды Арбата
274140104             наземная                          Новопесковский, 2000
273798495              Unknown                   Дом на Композиторской, 2006
274018110            подземная                            Филипповский, 2002
273785180              Unknown                                      The Book
273785183              Unknown                                      The Book
273785185              Unknown                                      The Book
273114736              Unknown                             Smolensky De Luxe
269319175            подземная                           Звёзды Арбата, 2013
261980888            подземная                           Звёзды Арбата, 2013
274930877            подземная                            Филипповский, 2002
271988698              Unknown                             Новый Арбат, 2010
271097684            подземная                       Smolensky De Luxe, 2015
270282698              Unknown                                The Book, 2020
271827359              Unknown                                 Звёзды Арбата
274434108              Unknown                                      The Book
272559990              Unknown                                 Звёзды Арбата
271627634              Unknown                                 Звёзды Арбата
274700592              Unknown                          Новопесковский, 2000
271586905              Unknown                                 Звёзды Арбата
272845144              Unknown                         Дом на Композиторской
274743086              Unknown                            Филипповский, 2002
271776317              Unknown                   Дом на Композиторской, 2006
274252226            подземная                          Новопесковский, 2000
229808794             наземная                                The Book, 2020
269317588              Unknown                                      The Book
236632140              Unknown                                The Book, 2020
271577440            подземная                                 Звёзды Арбата
273795577              Unknown                          Русский модерн, 2006
272262503         

In [32]:
df['Название ЖК'].fillna('Unknown', inplace=True)

In [33]:
df['Название ЖК'] = df['Название ЖК'].apply(lambda x: x.split(',')[0])

In [37]:
df[df['Название ЖК'].isin(df[(df['Парковка'] == 'Unknown') & (~df['Название ЖК'].isna())]['Название ЖК'])][['Парковка','Название ЖК']]

Парковка                         Название ЖК
ID  объявления                                                    
271271157            подземная                         Новый Арбат
271634126            подземная                         Новый Арбат
271173086            подземная                         Новый Арбат
272197456            подземная                             Unknown
273614615              Unknown                            The Book
274837728              Unknown                   Smolensky De Luxe
273643908             наземная                             Unknown
274475342            подземная                             Unknown
273973191             открытая                             Unknown
272900409             открытая                             Unknown
271036964            подземная                             Unknown
273999490              Unknown                             Unknown
274017037              Unknown                             Unknown
273231024              Unknown                             Unknown
274839211            подземная                        Филипповский
274767901              Unknown                        Филипповский
274995950              Unknown                            The Book
274945807              Unknown                        Филипповский
272911145             наземная                             Unknown
274748017              Unknown                             Unknown
273941734              Unknown                            The Book
274493570            подземная                             Unknown
274849101              Unknown                             Unknown
223918678              Unknown                        Филипповский
274391259             открытая                             Unknown
272945376             наземная                      Русский модерн
272612966              Unknown                             Unknown
271568490              Unknown                             Unknown
264664760              Unknown                       Звёзды Арбата
228923308            подземная                        Филипповский
267489303             открытая                             Unknown
273353104            подземная                       Звёзды Арбата
273353103            подземная                       Звёзды Арбата
268321690            подземная                       Звёзды Арбата
269496185            подземная                             Unknown
272188531              Unknown                            The Book
272727784              Unknown                             Unknown
267110043              Unknown                   Smolensky De Luxe
265323319            подземная                       Звёзды Арбата
265804792              Unknown                             Unknown
239000408              Unknown                             Unknown
271209314              Unknown                         Новый Арбат
269889430              Unknown                             Unknown
241704098              Unknown                         Новый Арбат
239000331              Unknown                        Филипповский
272823500            подземная                             Unknown
271265359             наземная                             Unknown
274289253              Unknown                             Unknown
274150874              Unknown                             Unknown
274849686            подземная                      Новопесковский
274315381              Unknown                        Филипповский
273779074              Unknown                             Unknown
274217247              Unknown                             Unknown
272156997             наземная                             Unknown
274617827              Unknown                             Unknown
269132104            подземная                       Звёзды Арбата
273911217              Unknown                             Unknown
274137125            подземная                      Новопесковский
27